<h1><center>461 - Assignment #2</center></h1>
<center>Name: Dion Olympia</center>
<center>UMBC ID: uy05130</center>
<center>Semester: Fall 2019</center>

## 1-A: What is an embedded database?
An embedded database is a database that is tightly integrated with the an application.  This means that the database management technology is built into the applications rather than having them as separate tools.


## 1-B: Name the popular embedded relational database:
<br>
<center>SQLite</center>
<br>

## 1-C: List two major differences between this and other popular RDBMS
1. It is a "serverless" database.  Most relational database management systems are implemented as a server process that the program communicates with.  However, in SQLite, processes that access the database will directly read from and write to the disk file.  This removes the need for managing configuration files or stopping/starting a server process.  Basically, SQLite is immediately ready for use and is user-friendly.
<br>
<br>
2. It is more portable than other database management systems.  Usually, data is stored in multiple files, but SQLite stores the entire database in a single file.  It's also lightweight, meaning it does not take a lot of space, hence the "lite" in its name.

## 2-A : Import ODBC/JDBC driver and establish database connectivity

In [1]:
import mysql.connector
cnx = mysql.connector.connect(user='root', password='',
                              host='localhost',
                              database='imdb')

## 2-B : Print the name of all actors who are known for at least four movies 

In [2]:
cursor = cnx.cursor()
q_b = ("SELECT name FROM (SELECT name, (LENGTH(known_for) - LENGTH(REPLACE(known_for,',',''))+1) as movies, IF(FIND_IN_SET('actor',profession) OR FIND_IN_SET('actress',profession),1,0) as acting FROM people GROUP BY id HAVING movies >=4 AND acting > 0) as a;")
cursor.execute(q_b)
for name in cursor:
    print(name);

('Fred Astaire',)
('Lauren Bacall',)
('Brigitte Bardot',)
('John Belushi',)
('Ingmar Bergman',)
('Ingrid Bergman',)
('Humphrey Bogart',)
('Marlon Brando',)
('Richard Burton',)
('James Cagney',)
('Gary Cooper',)
('Bette Davis',)
('Doris Day',)
('Olivia de Havilland',)
('James Dean',)
('Marlene Dietrich',)
('Kirk Douglas',)
('Henry Fonda',)
('Joan Fontaine',)
('Clark Gable',)
('Judy Garland',)
('John Gielgud',)
('Cary Grant',)
('Alec Guinness',)
('Rita Hayworth',)
('Margaux Hemingway',)
('Audrey Hepburn',)
('Katharine Hepburn',)
('Charlton Heston',)
('Alfred Hitchcock',)
('William Holden',)
('Buster Keaton',)
('Gene Kelly',)
('Grace Kelly',)
('Deborah Kerr',)
('Alan Ladd',)
('Veronica Lake',)
('Burt Lancaster',)
('Bruce Lee',)
('Vivien Leigh',)
('Sophia Loren',)
('Peter Lorre',)
('Groucho Marx',)
('James Mason',)
('Marcello Mastroianni',)
('Robert Mitchum',)
('Marilyn Monroe',)
('Paul Newman',)
('David Niven',)
("Maureen O'Hara",)
('Laurence Olivier',)
('Gregory Peck',)
('Tyrone Power',)

In [3]:
cursor.close()
cnx.close()

## 2-C : Establish new connection & ask user for an actor's name 

In [4]:

new_cnx = mysql.connector.connect(user='root', password='',
                              host='localhost',
                              database='imdb')
new_cursor = new_cnx.cursor()

actor = input("Insert an actor's name:\n")
# For my notebook, I used the actor "G.W. Bizter"


Insert an actor's name:
G.W. Bitzer


## 2-C.1 : Names of actors that have acted in movies that this actor is known for. 

In [5]:
q_c1 = ("SELECT name FROM people WHERE (FIND_IN_SET(SUBSTRING_INDEX(SUBSTRING_INDEX((SELECT known_for FROM people WHERE name = %s) ,',',1),',',-1), known_for) OR FIND_IN_SET(SUBSTRING_INDEX(SUBSTRING_INDEX((SELECT known_for FROM people WHERE name = %s) ,',',2),',',-1), known_for) OR FIND_IN_SET(SUBSTRING_INDEX(SUBSTRING_INDEX((SELECT known_for FROM people WHERE name = %s) ,',',3),',',-1), known_for) OR FIND_IN_SET(SUBSTRING_INDEX(SUBSTRING_INDEX((SELECT known_for FROM people WHERE name = %s) ,',',4),',',-1), known_for)) AND (FIND_IN_SET('actor', profession) OR FIND_IN_SET('actress',profession));")
cursor1 = new_cnx.cursor()
cursor1.execute(q_c1, (actor,actor,actor,actor))
for name in cursor1:
    print(name)

('Erville Alderson',)
('Frank Bennett',)
('Kate Bruce',)
('William E. Cassidy',)
('Hazel Childers',)
('Miriam Cooper',)
('Josephine Crowell',)
('Ruth Darling',)
('Dore Davidson',)
('Sam De Grasse',)
('Carol Dempster',)
('Taylor N. Duncan',)
('Pearl Elmore',)
('Mary Foy',)
('Howard Gaye',)
('Olga Grey',)
('Ruth Handforth',)
('Robert Harron',)
('Joseph Henabery',)
('Lloyd Ingraham',)
('Lucille La Verne',)
('Lillian Langdon',)
('W.E. Lawrence',)
('Walter Long',)
('Bessie Love',)
('Julia Mackley',)
('Mae Marsh',)
('A.W. McClure',)
('Leo Nomis',)
('Alfred Paget',)
('Allan Sears',)
('Clarine Seymour',)
('Mike Siebert',)
('Maxfield Stanley',)
('Porter Strong',)
('Herbert Sutch',)
('Constance Talmadge',)
('Jane Thomas',)
('F.A. Turner',)
('Erich von Ritzau',)
('Eleanor Washington',)
('Lucille Browne',)
('Grace Wilson',)
('Charles Eagle Eye',)
('Louis Romaine',)
('Ah Singh',)
('Shorty English',)
('John Bragdon',)
('James Burns',)


## 2-C.2 : Mean, Median & Mode of the actor's movie ratings

### Mean:

In [6]:
q_c2i = ("SELECT avg(avg_rating) FROM (SELECT title, avg_rating FROM titles INNER JOIN (SELECT * FROM ratings WHERE FIND_IN_SET(movieid, (SELECT known_for FROM people WHERE name = %s))) a ON titleid = movieid) as a;")
cursor2 = new_cnx.cursor()
cursor2.execute(q_c2i, (actor,))
for rating in cursor2:
    print(rating)

(Decimal('6.6667'),)


### Median:

In [7]:
q_c2ii = ("SELECT AVG(dd.avg_rating) as median FROM (SELECT d.avg_rating, @rownum:=@rownum+1 as `row_number`, @total_rows:=@rownum FROM (SELECT title, avg_rating FROM titles INNER JOIN (SELECT * FROM ratings WHERE FIND_IN_SET(movieid, (SELECT known_for FROM people WHERE name = %s))) a ON titleid = movieid) as d, (SELECT @rownum:=0) r WHERE d.avg_rating is NOT NULL ORDER BY d.avg_rating) as dd WHERE dd.row_number IN ( FLOOR((@total_rows+1)/2), FLOOR((@total_rows+2)/2) );")
cursor2=new_cnx.cursor()
cursor2.execute(q_c2ii, (actor,))
for rating in cursor2:
    print(rating)

(Decimal('7.0000'),)


### Mode(s):

In [8]:
q_c2iii = ("SELECT avg_rating FROM (SELECT title, avg_rating, COUNT(avg_rating) as frequency FROM titles INNER JOIN (SELECT * FROM ratings WHERE FIND_IN_SET(movieid, (SELECT known_for FROM people WHERE name = %s))) a ON titleid = movieid GROUP BY title) as z WHERE frequency = (SELECT MAX(frequency) FROM  (SELECT title, avg_rating, COUNT(avg_rating) as frequency FROM titles INNER JOIN (SELECT * FROM ratings WHERE FIND_IN_SET(movieid, (SELECT known_for FROM people WHERE name = %s))) a ON titleid = movieid GROUP BY title) as y);")
cursor2 = new_cnx.cursor()
cursor2.execute(q_c2iii, (actor,actor))
for rating in cursor2:
    print(rating)

(Decimal('8'),)
(Decimal('7'),)
(Decimal('5'),)


## 2-C.3 : Actor's highest rated movie

In [9]:
q_c3 = ("SELECT title FROM titles INNER JOIN (SELECT titleid, MAX(avg_rating) FROM (SELECT titleid, movieid, avg_rating FROM titles INNER JOIN ratings ON titleid = movieid WHERE FIND_IN_SET(movieid, (SELECT known_for FROM people WHERE name = %s LIMIT 1))) as a) as b ON titles.titleid = b.titleid LIMIT 1;")
cursor3 = new_cnx.cursor()
cursor3.execute(q_c3, (actor,))
print(cursor3.fetchone())

('Intolerance: A Sun-Play of the Ages',)


## 2-C.4: Legit check

In [10]:
q_c4 = ("SELECT IF(((SELECT movieid FROM (SELECT movieid, MAX(avg_rating) FROM (SELECT * FROM ratings WHERE FIND_IN_SET(movieid, (SELECT known_for FROM people WHERE name = %s)))as a) as b) = (SELECT movieid FROM (SELECT movieid, MAX(votes) FROM (SELECT * FROM ratings WHERE FIND_IN_SET(movieid, (SELECT known_for FROM people WHERE name = %s)))as c) as d)), 'Legit', (SELECT title FROM titles INNER JOIN (SELECT movieid FROM (SELECT movieid, MAX(votes) FROM (SELECT * FROM ratings WHERE FIND_IN_SET(movieid, (SELECT known_for FROM people WHERE name = %s)))as e) as f) as g ON movieid = titleid)) as output;")
cursor4 = new_cnx.cursor()
cursor4.execute(q_c4, (actor,actor,actor))
print(cursor4.fetchone())

('Legit',)


## 3. Julian Assange (Code Contribution)

Julian Assange has contributed code to the Postgres DBMS:  
https://git.postgresql.org/gitweb/?p=postgresql.git;a=search;h=HEAD;s=Julian+Assange;st=author